# 1. Load packages

The link to get [ImageAnalysis3](https://github.com/zhengpuas47/ImageAnalysis3) 

or the Zhuang lab archived [source_tools](https://github.com/ZhuangLab/Chromatin_Analysis_2020_cell/tree/master/sequential_tracing/source)

In [4]:
%run "C:\Users\shiwei\Documents\ImageAnalysis3\required_files\Startup_py3.py"
sys.path.append(r"C:\Users\shiwei\Documents")

import ImageAnalysis3 as ia
%matplotlib notebook

from ImageAnalysis3 import *
print(os.getpid())

import h5py
from ImageAnalysis3.classes import _allowed_kwds
import ast

import pandas as pd

21196


See **functions** in the repository for [AnalysisTool_Chromatin](../../functions/README.md)

In [5]:
# Chromatin_analysis_tools (ATC)
# Get path for the py containing functions
import os
import sys
import importlib
module_path =r'C:\Users\shiwei\Documents\AnalysisTool_Chromatin'
if module_path not in sys.path:
    sys.path.append(module_path)
    
# import relevant modules
import gene_selection 
importlib.reload(gene_selection)
import gene_to_loci
importlib.reload(gene_to_loci)
import gene_activity
importlib.reload(gene_activity)
import loci_1d_features
importlib.reload(loci_1d_features)  

import atac_to_loci
importlib.reload(atac_to_loci)

<module 'atac_to_loci' from 'C:\\Users\\shiwei\\Documents\\AnalysisTool_Chromatin\\atac_to_loci.py'>

In [6]:
import seaborn as sns
import scanpy as sc

## 1.1 Define output folder

In [7]:
output_main_folder = r'L:\Shiwei\Figures\MOp_draft_2023_v2\AB_compartment_th_zero'
output_analysis_folder = os.path.join(output_main_folder, 'analysis')
output_figure_folder = os.path.join(output_main_folder, 'figures')

make_output_folder = True

if make_output_folder and not os.path.exists(output_analysis_folder):
    os.makedirs(output_analysis_folder)
    print(f'Generating analysis folder: {output_analysis_folder}.')
elif os.path.exists(output_analysis_folder):
    print(f'Use existing analysis folder: {output_analysis_folder}.')
    
if make_output_folder and not os.path.exists(output_figure_folder):
    os.makedirs(output_figure_folder)
    print(f'Generating figure folder: {output_figure_folder}.')
elif os.path.exists(output_figure_folder):
    print(f'Use existing figure folder: {output_figure_folder}.')


Use existing analysis folder: L:\Shiwei\Figures\MOp_draft_2023_v2\AB_compartment_th_zero\analysis.
Use existing figure folder: L:\Shiwei\Figures\MOp_draft_2023_v2\AB_compartment_th_zero\figures.


## 1.2 setting up plotting parameters

In [8]:
import matplotlib
matplotlib.rcParams['pdf.fonttype'] = 42
import matplotlib.pyplot as plt
plt.rc('font', family='serif')
plt.rc('font', serif='Arial')

from ImageAnalysis3.figure_tools import _double_col_width, _single_col_width, _font_size, _ticklabel_size,_ticklabel_width

import seaborn as sns
sns.set_context("paper", rc={"font.size":_font_size,"axes.titlesize":_font_size+1,"axes.labelsize":_font_size})  

In [9]:
# cell labels from RNA-MERFISH and celltype prediction
selected_cell_labels = ['L2/3 IT','L4/5 IT','L5 IT','L6 IT','L5 ET','L5/6 NP','L6 CT','L6b',
                           'Sst','Pvalb','Lamp5','Sncg','Vip',
                           'Astro','Oligo','OPC','Micro','Endo','VLMC','SMC','Peri', 
                           #'other',
                          ]
# cell palette from RNA-MERFISH UMAP and stats
celltype_palette = {'Astro':'lightcoral', 
                    'Endo':'skyblue', 
                    'L2/3 IT':'gold', 
                    'L4/5 IT':'darkorange', 
                    'L5 ET':'mediumseagreen', 
                    'L5 IT':'aqua',
                    'L5/6 NP':'darkgreen',
                    'L6 CT':'brown',
                    'L6 IT':'magenta',
                    'L6b':'blue', 
                    'Lamp5':'orange', 
                    'Micro':'peachpuff',
                    'OPC':'thistle', 
                    'Oligo':'darkviolet',
                    'Peri':'sandybrown',
                    'Pvalb':'springgreen',
                    'SMC':'rosybrown',
                    'Sncg':'darkkhaki',
                    'Sst':'steelblue', 
                    'VLMC':'saddlebrown', 
                    'Vip':'red',
                    'other':'slategray'}


In [10]:
# this is the plotting order noted based on the snRNA transcriptional acitivty;
# we'd use this for all the graphs in this notebook
# use the snRNA data below (# section 3.1.1) if needs to re-calculate
sorted_cellplot_order = ['Micro', 'Oligo', 'Endo', 'OPC', 'Astro', 'Vip', 'Lamp5',
                  'L5/6 NP', 'Sst', 'Sncg', 'Pvalb', 'L4/5 IT', 'L6 CT',
                  'L6 IT', 'L6b', 'L2/3 IT', 'L5 IT', 'L5 ET']

# 2. Load codebook

## Codebook

Example of [codebook](../../postanalysis/0_locus_annotation/resources/MERFISH_loci_adjacent_genes_tss_more_res.csv)

In [11]:
# load codebook
# L drive is Crick Pu_SSD_0
codebook_save_folder=r'C:\Users\shiwei\Documents\AnalysisTool_Chromatin\resources'

# Load sorted codebook (allows direct matrix slicing) with cell type info
# Load codebook (then sort to allow direct matrix slicing) with cell type info

codebook_fname = os.path.join(codebook_save_folder,'MERFISH_loci_adjacent_genes_tss_more_res.csv')
codebook_df = pd.read_csv (codebook_fname, index_col=0)

# sort df temporailiy so matrix can be sliced by df order directly
codebook_df = loci_1d_features.sort_loci_df_by_chr_order (codebook_df)

codebook_df.head()

name id chr  chr_order library  dtype  \
loci_name                                                                  
chr1_3742742_3759944  1:3742742-3759944  1   1          0   CTP11  combo   
chr1_6245958_6258969  1:6245958-6258969  2   1          1   CTP11  combo   
chr1_8740008_8759916  1:8740008-8759916  3   1          2   CTP11  combo   
chr1_9627926_9637875  1:9627926-9637875  1   1          3   CTP13  combo   
chr1_9799472_9811359  1:9799472-9811359  2   1          4   CTP13  combo   

                     adjacent_genes_0kb_tss adjacent_genes_10kb_tss  \
loci_name                                                             
chr1_3742742_3759944             intergenic              intergenic   
chr1_6245958_6258969             intergenic              intergenic   
chr1_8740008_8759916             intergenic              intergenic   
chr1_9627926_9637875          2610203C22Rik           2610203C22Rik   
chr1_9799472_9811359                 Gm6195            Gm6195; Sgk3   

                     adjacent_genes_50kb_tss  \
loci_name                                      
chr1_3742742_3759944              intergenic   
chr1_6245958_6258969   4732440D04Rik; Rb1cc1   
chr1_8740008_8759916                 Gm15452   
chr1_9627926_9637875           2610203C22Rik   
chr1_9799472_9811359            Gm6195; Sgk3   

                                               adjacent_genes_100kb_tss  \
loci_name                                                                 
chr1_3742742_3759944                                               Xkr4   
chr1_6245958_6258969                              4732440D04Rik; Rb1cc1   
chr1_8740008_8759916                                            Gm15452   
chr1_9627926_9637875         2610203C22Rik; Adhfe1; Gm6161; Mybl1; Rrs1   
chr1_9799472_9811359  1700034P13Rik; Gm6195; Mcmdc2; Mybl1; Sgk3; Vc...   

                                               adjacent_genes_200kb_tss  \
loci_name                                                                 
chr1_3742742_3759944                                               Xkr4   
chr1_6245958_6258969             4732440D04Rik; Gm19026; Gm2147; Rb1cc1   
chr1_8740008_8759916                                            Gm15452   
chr1_9627926_9637875  1700034P13Rik; 2610203C22Rik; Adhfe1; Gm18300;...   
chr1_9799472_9811359  1700034P13Rik; 2610203C22Rik; Gm6195; Mcmdc2; ...   

                                               adjacent_genes_500kb_tss  \
loci_name                                                                 
chr1_3742742_3759944                              Gm18956; Gm7341; Xkr4   
chr1_6245958_6258969  4732440D04Rik; Gm19026; Gm2147; Npbwr1; Rb1cc1...   
chr1_8740008_8759916                                            Gm15452   
chr1_9627926_9637875  1700034P13Rik; 2610203C22Rik; Adhfe1; Cops5; C...   
chr1_9799472_9811359  1700034P13Rik; 2610203C22Rik; Adhfe1; Arfgef1;...   

                                              adjacent_genes_1000kb_tss  \
loci_name                                                                 
chr1_3742742_3759944  Gm18956; Gm2053; Gm6085; Gm6101; Gm6119; Gm734...   
chr1_6245958_6258969  4732440D04Rik; Gm19026; Gm2147; Gm5694; Gm7182...   
chr1_8740008_8759916  1700034P13Rik; 2610203C22Rik; Adhfe1; Gm15452;...   
chr1_9627926_9637875  1700034P13Rik; 2610203C22Rik; Adhfe1; Arfgef1;...   
chr1_9799472_9811359  1700034P13Rik; 2610203C22Rik; Adhfe1; Arfgef1;...   

                                              adjacent_genes_1500kb_tss  \
loci_name                                                                 
chr1_3742742_3759944  Atp6v1h; Gm16041; Gm17101; Gm18956; Gm2053; Gm...   
chr1_6245958_6258969  4732440D04Rik; Atp6v1h; Gm16041; Gm17101; Gm19...   
chr1_8740008_8759916  1700034P13Rik; 2610203C22Rik; Adhfe1; Arfgef1;...   
chr1_9627926_9637875  1700034P13Rik; 2610203C22Rik; Adhfe1; Arfgef1;...   
chr1_9799472_9811359  1700034P13Rik; 2610203C22Rik; Adhfe1; Arfgef1;...   

                                     

## Refgen for gene dist matrix

Example of [refgen](../0_locus_annotation/resources/refgen_df_for_jie.csv)

In [12]:
codebook_folder = r'\\10.245.74.158\Chromatin_NAS_8\Analyzed_data\MouseBrain_PostAnalysis'
df_refgen_savename = os.path.join(codebook_folder,'refgen_df_for_jie.csv')
df_refgen=pd.read_csv(df_refgen_savename,index_col=0)
df_refgen['chr'] = df_refgen['chr'].apply(lambda x: 'chr'+x)
df_refgen.head()

name id   chr  chr_order library  dtype             loci_name  \
0  1:3742742-3759944  1  chr1          0   CTP11  combo  chr1_3742742_3759944   
1  1:6245958-6258969  2  chr1          1   CTP11  combo  chr1_6245958_6258969   
2  1:8740008-8759916  3  chr1          2   CTP11  combo  chr1_8740008_8759916   
3  1:9627926-9637875  1  chr1          3   CTP13  combo  chr1_9627926_9637875   
4  1:9799472-9811359  2  chr1          4   CTP13  combo  chr1_9799472_9811359   

     start      end  hyb    delta  region_id  
0  3742742  3759944    0        0          1  
1  6245958  6258969    1  2503216          2  
2  8740008  8759916    2  4997266          3  
3  9627926  9637875    3  5885184          4  
4  9799472  9811359    4  6056730          5

In [13]:
chrom_number = []
for i, row in df_refgen.iterrows():
    if ('X' in row.chr):
        chrom_number.append(20)
    elif ('Y' in row.chr):
        chrom_number.append(21)
    else:
        chrom_number.append(int(row['chr'].split('chr')[-1]))
df_refgen['chrom_number'] = chrom_number
df_refgen.sort_values(['chrom_number','hyb'], inplace=True, ignore_index=True)
df_refgen.head()

name id   chr  chr_order library  dtype             loci_name  \
0  1:3742742-3759944  1  chr1          0   CTP11  combo  chr1_3742742_3759944   
1  1:6245958-6258969  2  chr1          1   CTP11  combo  chr1_6245958_6258969   
2  1:8740008-8759916  3  chr1          2   CTP11  combo  chr1_8740008_8759916   
3  1:9627926-9637875  1  chr1          3   CTP13  combo  chr1_9627926_9637875   
4  1:9799472-9811359  2  chr1          4   CTP13  combo  chr1_9799472_9811359   

     start      end  hyb    delta  region_id  chrom_number  
0  3742742  3759944    0        0          1             1  
1  6245958  6258969    1  2503216          2             1  
2  8740008  8759916    2  4997266          3             1  
3  9627926  9637875    3  5885184          4             1  
4  9799472  9811359    4  6056730          5             1

In [14]:
from scipy.spatial.distance import squareform, pdist
chr_gene_dist_matrices = {}
for chrom, df_chr in df_refgen.groupby('chr'):
    if 'Y' not in chrom:
        _df = df_chr.sort_values('hyb')
        _delta_values= np.zeros((len(_df),2))
        _delta_values[:,0] = _df.delta.values
        _gene_dist = squareform(pdist(_delta_values))
        chr_gene_dist_matrices[chrom] = _gene_dist

# 3. Load AB density ratio

Data can be generated from notebook 

[5_compute_ab_trans_density_singlecelll_subclass](5_compute_ab_trans_density_singlecelll_subclass.ipynb)

In [15]:
import pickle
gaussian_radius= 0.5
transABratio_ensemble_filename = os.path.join(output_analysis_folder, f'trans_AB_ratio_notNorm_r{gaussian_radius}_bysubclass_th_zero.pkl')
if os.path.exists(transABratio_ensemble_filename):
    print(transABratio_ensemble_filename)
    trans_AB_ratio_by_group = pickle.load(open(transABratio_ensemble_filename, 'rb'))

L:\Shiwei\Figures\MOp_draft_2023_v2\AB_compartment_th_zero\analysis\trans_AB_ratio_notNorm_r0.5_bysubclass_th_zero.pkl


In [16]:
trans_AB_ratio_by_group.keys()

dict_keys(['Oligo', 'OPC', 'Micro', 'Astro', 'Endo', 'L2/3 IT', 'L4/5 IT', 'L5 IT', 'L6 IT', 'L5 ET', 'L6 CT', 'L5/6 NP', 'L6b', 'Vip', 'Pvalb', 'Lamp5', 'Sst', 'Sncg'])

# 4. Calculate median ratio for all qualified cells

In [17]:
%matplotlib inline

import gene_activity
import loci_1d_features
from scipy import stats
import seaborn as sns
from tqdm import tqdm

#bin_size =500 # extend both way, thus equivilant to~ 1Mb
#adjcent_col = f'Adjacent_genes_{bin_size}kb_tss'
#activity_type = 'sum' # mean of each gene associated to a loci for single cell
#codebook_df = celltype_codebook_df

# the grouby in adata (to distinguish the grouby_savename for the saved dataframe)
groupby_adata = 'class_label_new'

#_group = 'Gluta'
#sorted_group_order = [_group]

calculate_ab = True

ABratio_dict = {}


loci_key_list = loci_1d_features.sorted_loci_keys_for_loci_dataframe(codebook_df)
#loci_ori_ind = loci_1d_features.find_chr_loci_iloc_from_loci_keys (codebook_df, loci_key_list)
        
# 2.2 trans
if calculate_ab:
    
    for _class in trans_AB_ratio_by_group.keys():
        print(f'Process {_class}')
        ABratio_dict[_class] = {}
        for _ind, sel_loci_ind in tqdm(enumerate(codebook_df.index.tolist()[:])):
            sel_loci_key = loci_key_list[_ind]
            transAB_ratios_df = loci_1d_features.sc_compartment_ratio_by_loci_key (trans_AB_ratio_by_group, 
                                                                       [_class], 
                                                                       sel_loci_key, 
                                                                    average_ratios_in_cell=True, 
                                                                                   spot_num_th=600,
                                                                                   report_type = 'median')
            ABratio_dict[_class][_ind]=list(transAB_ratios_df[_class])


Process Oligo


0it [00:00, ?it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
1it [00:00,  1.17it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
2it [00:01,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
3it [00:02,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
4it [00:03,  1.18it/s]C:\Users\shiwei\Docume

34it [00:28,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
35it [00:29,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
36it [00:30,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
37it [00:31,  1.19it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
38it [00:32,  1.19it/s]C:\Users\shiw

68it [00:57,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
69it [00:58,  1.19it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
70it [00:59,  1.19it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
71it [00:59,  1.19it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
72it [01:00,  1.19it/s]C:\Users\shiw

102it [01:26,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
103it [01:26,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
104it [01:27,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
105it [01:28,  1.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
106it [01:29,  1.18it/s]C:\Users

...

1800it [00:34, 51.38it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty

1842it [00:35, 51.18it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty

1884it [00:36, 51.40it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty

1926it [00:37, 51.52it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty

1968it [00:38, 51.52it/s]C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty slice
  mean_ratio_cell = np.nanmean(np.array(loci_ratio_cell)) # warning raised here: nanmean of nans return nan
C:\Users\shiwei\Documents\AnalysisTool_Chromatin\loci_1d_features.py:319: RuntimeWarning: Mean of empty

In [18]:
ABratio_dict.keys()

dict_keys(['Oligo', 'OPC', 'Micro', 'Astro', 'Endo', 'L2/3 IT', 'L4/5 IT', 'L5 IT', 'L6 IT', 'L5 ET', 'L6 CT', 'L5/6 NP', 'L6b', 'Vip', 'Pvalb', 'Lamp5', 'Sst', 'Sncg'])

## Save the median AB ratio by type

In [19]:
codebook_df.index

Index(['chr1_3742742_3759944', 'chr1_6245958_6258969', 'chr1_8740008_8759916',
       'chr1_9627926_9637875', 'chr1_9799472_9811359',
       'chr1_11247744_11257616', 'chr1_13741888_13757922',
       'chr1_16251322_16259969', 'chr1_18749330_18759924',
       'chr1_20920666_20929358',
       ...
       'chrX_153743904_153759903', 'chrX_156242675_156257265',
       'chrX_158749404_158759978', 'chrX_161247067_161259813',
       'chrX_163750534_163758706', 'chrX_166247682_166259932',
       'chrX_167157164_167167452', 'chrX_168746045_168757590',
       'chrX_169963295_170005197', 'chrY_1245775_1259992'],
      dtype='object', name='loci_name', length=1982)

In [20]:
ABratio_df_list = []


for _sel_class in ABratio_dict.keys():

    ABratio_df = pd.DataFrame.from_dict(ABratio_dict[_sel_class])
    ABratio_df_list.append(ABratio_df)
    
ABratio_dfs = pd.concat(ABratio_df_list)
if len(ABratio_dfs) == len(list(ABratio_dict.keys())):
    ABratio_dfs.index = list(ABratio_dict.keys())

if len(ABratio_dfs.columns) == len(codebook_df.index):
    ABratio_dfs.columns = codebook_df.index
ABratio_dfs

loci_name  chr1_3742742_3759944  chr1_6245958_6258969  chr1_8740008_8759916  \
Oligo                 -0.422395             -0.123587             -0.384446   
OPC                   -0.336774             -0.183419             -0.052034   
Micro                 -0.278088             -0.065169             -0.286666   
Astro                 -0.489602             -0.251864             -0.411412   
Endo                   0.087817              0.346057              0.014480   
L2/3 IT               -0.474198             -0.384096             -0.355418   
L4/5 IT               -0.424039             -0.395186             -0.283315   
L5 IT                 -0.397661             -0.374351             -0.337409   
L6 IT                 -0.433375             -0.342256             -0.340426   
L5 ET                 -0.406431             -0.363363             -0.234319   
L6 CT                 -0.441964             -0.392261             -0.418353   
L5/6 NP               -0.261607             -0.175218             -0.480288   
L6b                   -0.355470             -0.197491             -0.499484   
Vip                   -0.242751             -0.301612              0.005046   
Pvalb                 -0.365409             -0.214871             -0.199206   
Lamp5                 -0.271475             -0.229265             -0.062207   
Sst                   -0.348622             -0.127568             -0.122095   
Sncg                  -0.396724             -0.257080             -0.540594   

loci_name  chr1_9627926_9637875  chr1_9799472_9811359  chr1_11247744_11257616  \
Oligo                 -0.229349             -0.079250               -0.298759   
OPC                   -0.036024             -0.062537               -0.292356   
Micro                  0.030728              0.222733               -0.262458   
Astro                 -0.166186             -0.080703               -0.022628   
Endo                   0.244415              0.478925                0.461947   
L2/3 IT               -0.300878             -0.249645               -0.509752   
L4/5 IT               -0.238133             -0.248266               -0.515674   
L5 IT                 -0.336847             -0.203845               -0.395429   
L6 IT                 -0.161302             -0.208270               -0.308787   
L5 ET                 -0.240122             -0.187555               -0.344334   
L6 CT                 -0.237506             -0.207870               -0.280182   
L5/6 NP               -0.296984             -0.272937               -0.125382   
L6b                   -0.294759             -0.285443               -0.251266   
Vip                   -0.280499             -0.315864               -0.108041   
Pvalb                 -0.201809             -0.393889               -0.300295   
Lamp5                 -0.023237             -0.104418               -0.161701   
Sst                   -0.200314             -0.167614               -0.224883   
Sncg                  -0.325647             -0.507851               -0.437713   

loci_name  chr1_13741888_13757922  chr1_16251322_16259969  \
Oligo                   -0.179830               -0.290425   
OPC                     -0.237733               -0.219124   
Micro                   -0.116052               -0.079124   
Astro                   -0.241726               -0.276326   
Endo                     0.172245                0.211113   
L2/3 IT                 -0.360944               -0.129925   
L4/5 IT                 -0.346251               -0.214730   
L5 IT                   -0.303623               -0.200631   
L6 IT                   -0.300889               -0.111071   
L5 ET                   -0.596209               -0.260709   
L6 CT                   -0.438749               -0.354415   
L5/6 NP                 -0.223126               -0.239672   
L6b                     -0.384684               -0.287323   
Vip                     -0.227730               -0.177885   
Pvalb                   -0.203173          

In [21]:
ABratio_dfs.transpose()

Oligo       OPC     Micro     Astro      Endo  \
loci_name                                                                    
chr1_3742742_3759944     -0.422395 -0.336774 -0.278088 -0.489602  0.087817   
chr1_6245958_6258969     -0.123587 -0.183419 -0.065169 -0.251864  0.346057   
chr1_8740008_8759916     -0.384446 -0.052034 -0.286666 -0.411412  0.014480   
chr1_9627926_9637875     -0.229349 -0.036024  0.030728 -0.166186  0.244415   
chr1_9799472_9811359     -0.079250 -0.062537  0.222733 -0.080703  0.478925   
...                            ...       ...       ...       ...       ...   
chrX_166247682_166259932  0.227213  0.121523  0.065605  0.364292  0.309217   
chrX_167157164_167167452  0.102458 -0.135584  0.430749  0.054695  0.556941   
chrX_168746045_168757590 -0.134512 -0.316071 -0.007819 -0.168453  0.254124   
chrX_169963295_170005197 -0.079956  0.124813  0.064583  0.029156  0.540016   
chrY_1245775_1259992           NaN       NaN       NaN       NaN       NaN   

                           L2/3 IT   L4/5 IT     L5 IT     L6 IT     L5 ET  \
loci_name                                                                    
chr1_3742742_3759944     -0.474198 -0.424039 -0.397661 -0.433375 -0.406431   
chr1_6245958_6258969     -0.384096 -0.395186 -0.374351 -0.342256 -0.363363   
chr1_8740008_8759916     -0.355418 -0.283315 -0.337409 -0.340426 -0.234319   
chr1_9627926_9637875     -0.300878 -0.238133 -0.336847 -0.161302 -0.240122   
chr1_9799472_9811359     -0.249645 -0.248266 -0.203845 -0.208270 -0.187555   
...                            ...       ...       ...       ...       ...   
chrX_166247682_166259932 -0.056365 -0.012575 -0.208386 -0.175914 -0.006859   
chrX_167157164_167167452 -0.123888 -0.062526 -0.143780 -0.118719 -0.155330   
chrX_168746045_168757590 -0.243110 -0.215402 -0.186746 -0.175388 -0.235237   
chrX_169963295_170005197 -0.190289 -0.220554 -0.244034 -0.318961 -0.223761   
chrY_1245775_1259992           NaN       NaN       NaN       NaN       NaN   

                             L6 CT   L5/6 NP       L6b       Vip     Pvalb  \
loci_name                                                                    
chr1_3742742_3759944     -0.441964 -0.261607 -0.355470 -0.242751 -0.365409   
chr1_6245958_6258969     -0.392261 -0.175218 -0.197491 -0.301612 -0.214871   
chr1_8740008_8759916     -0.418353 -0.480288 -0.499484  0.005046 -0.199206   
chr1_9627926_9637875     -0.237506 -0.296984 -0.294759 -0.280499 -0.201809   
chr1_9799472_9811359     -0.207870 -0.272937 -0.285443 -0.315864 -0.393889   
...                            ...       ...       ...       ...       ...   
chrX_166247682_166259932 -0.067705  0.058149  0.053279 -0.145523 -0.236549   
chrX_167157164_167167452 -0.107538  0.072693 -0.160688  0.084008 -0.043039   
chrX_168746045_168757590 -0.294560  0.249351 -0.281637 -0.231542 -0.059648   
chrX_169963295_170005197 -0.311680 -0.025918 -0.114135 -0.251041 -0.095843   
chrY_1245775_1259992           NaN       NaN       NaN       NaN       NaN   

                             Lamp5       Sst      Sncg  
loci_name                                               
chr1_3742742_3759944     -0.271475 -0.348622 -0.396724  
chr1_6245958_6258969     -0.229265 -0.127568 -0.257080  
chr1_8740008_8759916     -0.062207 -0.122095 -0.540594  
chr1_9627926_9637875     -0.023237 -0.200314 -0.325647  
chr1_9799472_9811359     -0.104418 -0.167614 -0.507851  
...                            ...       ...       ...  
chrX_166247682_166259932 -0.223829 -0.154113 -0.555910  
chrX_167157164_167167452 -0.279229 -0.138286 -0.334614  
chrX_168746045_168757590 -0.344906 -0.176298 -0.444930  
chrX_169963295_170005197 -0.342024 -0.191063 -0.196725  
chrY_1245775_1259992           NaN       NaN       NaN  

[1982 rows x 18 columns]

In [22]:
#'transABRatio_cwAB_ATACcorr_notNorm_r0.5_byclass.pkl'

In [23]:
ABratio_dfs_fname = os.path.join(output_analysis_folder, r'Median_Summary_trans_AB_ratio_notNorm_r0.5_bysubclass_th_zero.csv')
ABratio_dfs.to_csv(ABratio_dfs_fname)